# Creating a Sentiment Analysis Web App
## Using PyTorch and SageMaker

_Deep Learning Nanodegree Program | Deployment_

---

Now that we have a basic understanding of how SageMaker works we will try to use it to construct a complete project from end to end. Our goal will be to have a simple web page which a user can use to enter a movie review. The web page will then send the review off to our deployed model which will predict the sentiment of the entered review.

## Instructions

Some template code has already been provided for you, and you will need to implement additional functionality to successfully complete this notebook. You will not need to modify the included code beyond what is requested. Sections that begin with '**TODO**' in the header indicate that you need to complete or implement some portion within them. Instructions will be provided for each section and the specifics of the implementation are marked in the code block with a `# TODO: ...` comment. Please be sure to read the instructions carefully!

In addition to implementing code, there will be questions for you to answer which relate to the task and your implementation. Each section where you will answer a question is preceded by a '**Question:**' header. Carefully read each question and provide your answer below the '**Answer:**' header by editing the Markdown cell.

> **Note**: Code and Markdown cells can be executed using the **Shift+Enter** keyboard shortcut. In addition, a cell can be edited by typically clicking it (double-click for Markdown cells) or by pressing **Enter** while it is highlighted.

## General Outline

Recall the general outline for SageMaker projects using a notebook instance.

1. Download or otherwise retrieve the data.
2. Process / Prepare the data.
3. Upload the processed data to S3.
4. Train a chosen model.
5. Test the trained model (typically using a batch transform job).
6. Deploy the trained model.
7. Use the deployed model.

For this project, you will be following the steps in the general outline with some modifications. 

First, you will not be testing the model in its own step. You will still be testing the model, however, you will do it by deploying your model and then using the deployed model by sending the test data to it. One of the reasons for doing this is so that you can make sure that your deployed model is working correctly before moving forward.

In addition, you will deploy and use your trained model a second time. In the second iteration you will customize the way that your trained model is deployed by including some of your own code. In addition, your newly deployed model will be used in the sentiment analysis web app.

## Step 1: Downloading the data

As in the XGBoost in SageMaker notebook, we will be using the [IMDb dataset](http://ai.stanford.edu/~amaas/data/sentiment/)

> Maas, Andrew L., et al. [Learning Word Vectors for Sentiment Analysis](http://ai.stanford.edu/~amaas/data/sentiment/). In _Proceedings of the 49th Annual Meeting of the Association for Computational Linguistics: Human Language Technologies_. Association for Computational Linguistics, 2011.

In [24]:
%mkdir ../data
!wget -O ../data/aclImdb_v1.tar.gz http://ai.stanford.edu/~amaas/data/sentiment/aclImdb_v1.tar.gz
!tar -zxf ../data/aclImdb_v1.tar.gz -C ../data

mkdir: cannot create directory ‘../data’: File exists
--2020-04-04 18:09:54--  http://ai.stanford.edu/~amaas/data/sentiment/aclImdb_v1.tar.gz
Resolving ai.stanford.edu (ai.stanford.edu)... 171.64.68.10
Connecting to ai.stanford.edu (ai.stanford.edu)|171.64.68.10|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 84125825 (80M) [application/x-gzip]
Saving to: ‘../data/aclImdb_v1.tar.gz’

../data/aclImdb_v1. 100%[===================>]  80.23M  22.3MB/s    in 5.1s    

2020-04-04 18:10:00 (15.7 MB/s) - ‘../data/aclImdb_v1.tar.gz’ saved [84125825/84125825]



## Step 2: Preparing and Processing the data

Also, as in the XGBoost notebook, we will be doing some initial data processing. The first few steps are the same as in the XGBoost example. To begin with, we will read in each of the reviews and combine them into a single input structure. Then, we will split the dataset into a training set and a testing set.

In [25]:
import os
import glob

def read_imdb_data(data_dir='../data/aclImdb'):
    data = {}
    labels = {}
    
    for data_type in ['train', 'test']:
        data[data_type] = {}
        labels[data_type] = {}
        
        for sentiment in ['pos', 'neg']:
            data[data_type][sentiment] = []
            labels[data_type][sentiment] = []
            
            path = os.path.join(data_dir, data_type, sentiment, '*.txt')
            files = glob.glob(path)
            
            for f in files:
                with open(f) as review:
                    data[data_type][sentiment].append(review.read())
                    # Here we represent a positive review by '1' and a negative review by '0'
                    labels[data_type][sentiment].append(1 if sentiment == 'pos' else 0)
                    
            assert len(data[data_type][sentiment]) == len(labels[data_type][sentiment]), \
                    "{}/{} data size does not match labels size".format(data_type, sentiment)
                
    return data, labels

In [26]:
data, labels = read_imdb_data()
print("IMDB reviews: train = {} pos / {} neg, test = {} pos / {} neg".format(
            len(data['train']['pos']), len(data['train']['neg']),
            len(data['test']['pos']), len(data['test']['neg'])))

IMDB reviews: train = 12500 pos / 12500 neg, test = 12500 pos / 12500 neg


Now that we've read the raw training and testing data from the downloaded dataset, we will combine the positive and negative reviews and shuffle the resulting records.

In [27]:
from sklearn.utils import shuffle

def prepare_imdb_data(data, labels):
    """Prepare training and test sets from IMDb movie reviews."""
    
    #Combine positive and negative reviews and labels
    data_train = data['train']['pos'] + data['train']['neg']
    data_test = data['test']['pos'] + data['test']['neg']
    labels_train = labels['train']['pos'] + labels['train']['neg']
    labels_test = labels['test']['pos'] + labels['test']['neg']
    
    #Shuffle reviews and corresponding labels within training and test sets
    data_train, labels_train = shuffle(data_train, labels_train)
    data_test, labels_test = shuffle(data_test, labels_test)
    
    # Return a unified training data, test data, training labels, test labets
    return data_train, data_test, labels_train, labels_test

In [28]:
train_X, test_X, train_y, test_y = prepare_imdb_data(data, labels)
print("IMDb reviews (combined): train = {}, test = {}".format(len(train_X), len(test_X)))

IMDb reviews (combined): train = 25000, test = 25000


Now that we have our training and testing sets unified and prepared, we should do a quick check and see an example of the data our model will be trained on. This is generally a good idea as it allows you to see how each of the further processing steps affects the reviews and it also ensures that the data has been loaded correctly.

In [29]:
print(train_X[100])
print(train_y[100])

Being S Club Seven, the film already boosts an ecstatic atmosphere! But seriously, Oprah has a point when claiming: "Don't go there, girl!" Spice World suddenly doesn't seem to be all that bad... I take my money elsewhere!
0


The first step in processing the reviews is to make sure that any html tags that appear should be removed. In addition we wish to tokenize our input, that way words such as *entertained* and *entertaining* are considered the same with regard to sentiment analysis.

In [30]:
import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import *

import re
from bs4 import BeautifulSoup

def review_to_words(review):
    nltk.download("stopwords", quiet=True)
    stemmer = PorterStemmer()
    
    text = BeautifulSoup(review, "html.parser").get_text() # Remove HTML tags
    text = re.sub(r"[^a-zA-Z0-9]", " ", text.lower()) # Convert to lower case
    words = text.split() # Split string into words
    words = [w for w in words if w not in stopwords.words("english")] # Remove stopwords
    words = [PorterStemmer().stem(w) for w in words] # stem
    
    return words

The `review_to_words` method defined above uses `BeautifulSoup` to remove any html tags that appear and uses the `nltk` package to tokenize the reviews. As a check to ensure we know how everything is working, try applying `review_to_words` to one of the reviews in the training set.

In [31]:
# TODO: Apply review_to_words to a review (train_X[100] or any other review)
review_to_words(train_X[10])

['direct',
 'clearli',
 'state',
 'film',
 'idea',
 'plot',
 'total',
 'origin',
 'howev',
 'read',
 'slam',
 'dunk',
 'comic',
 'clearli',
 'see',
 'charact',
 'similar',
 'even',
 'joke',
 'anoth',
 'note',
 'jay',
 'chow',
 'know',
 'kung',
 'fu',
 'impress',
 'anyon',
 'tri',
 'act',
 'like',
 'mani',
 'peopl',
 'today',
 'see',
 'differ',
 'luckili',
 'movi',
 'contain',
 'much',
 'kung',
 'fu',
 'fight',
 'much',
 'enchanc',
 'stunner',
 'visual',
 'effect',
 'think',
 'jay',
 'act',
 'still',
 'pain',
 'watch',
 'especi',
 'almost',
 'everyon',
 'els',
 'film',
 'much',
 'better',
 'reason',
 'think',
 'jay',
 'main',
 'actor',
 'simpli',
 'popular',
 'despit',
 'hard',
 'wish',
 'stop',
 'anyon',
 'watch',
 'thu',
 'make',
 'orgin',
 'movi',
 'get',
 'becam',
 'one',
 'best',
 'budget',
 'film',
 'china',
 'year']

**Question:** Above we mentioned that `review_to_words` method removes html formatting and allows us to tokenize the words found in a review, for example, converting *entertained* and *entertaining* into *entertain* so that they are treated as though they are the same word. What else, if anything, does this method do to the input?

**Answer:**

The method below applies the `review_to_words` method to each of the reviews in the training and testing datasets. In addition it caches the results. This is because performing this processing step can take a long time. This way if you are unable to complete the notebook in the current session, you can come back without needing to process the data a second time.

In [32]:
import pickle

cache_dir = os.path.join("../cache", "sentiment_analysis")  # where to store cache files
os.makedirs(cache_dir, exist_ok=True)  # ensure cache directory exists

def preprocess_data(data_train, data_test, labels_train, labels_test,
                    cache_dir=cache_dir, cache_file="preprocessed_data_full.pkl"):
    """Convert each review to words; read from cache if available."""

    # If cache_file is not None, try to read from it first
    cache_data = None
    if cache_file is not None:
        try:
            with open(os.path.join(cache_dir, cache_file), "rb") as f:
                cache_data = pickle.load(f)
            print("Read preprocessed data from cache file:", cache_file)
        except:
            pass  # unable to read from cache, but that's okay
    
    # If cache is missing, then do the heavy lifting
    if cache_data is None:
        # Preprocess training and test data to obtain words for each review
        #words_train = list(map(review_to_words, data_train))
        #words_test = list(map(review_to_words, data_test))
        words_train = [review_to_words(review) for review in data_train]
        words_test = [review_to_words(review) for review in data_test]
        
        # Write to cache file for future runs
        if cache_file is not None:
            cache_data = dict(words_train=words_train, words_test=words_test,
                              labels_train=labels_train, labels_test=labels_test)
            with open(os.path.join(cache_dir, cache_file), "wb") as f:
                pickle.dump(cache_data, f)
            print("Wrote preprocessed data to cache file:", cache_file)
    else:
        # Unpack data loaded from cache file
        words_train, words_test, labels_train, labels_test = (cache_data['words_train'],
                cache_data['words_test'], cache_data['labels_train'], cache_data['labels_test'])
    
    return words_train, words_test, labels_train, labels_test

In [33]:
# Preprocess data
#n=100
#train_X, test_X, train_y, test_y = preprocess_data(train_X[:n], test_X[:n], train_y[:n], test_y[:n])
train_X, test_X, train_y, test_y = preprocess_data(train_X, test_X, train_y, test_y)

Read preprocessed data from cache file: preprocessed_data_full.pkl


In [34]:
len(train_y)

25000

## Transform the data

In the XGBoost notebook we transformed the data from its word representation to a bag-of-words feature representation. For the model we are going to construct in this notebook we will construct a feature representation which is very similar. To start, we will represent each word as an integer. Of course, some of the words that appear in the reviews occur very infrequently and so likely don't contain much information for the purposes of sentiment analysis. The way we will deal with this problem is that we will fix the size of our working vocabulary and we will only include the words that appear most frequently. We will then combine all of the infrequent words into a single category and, in our case, we will label it as `1`.

Since we will be using a recurrent neural network, it will be convenient if the length of each review is the same. To do this, we will fix a size for our reviews and then pad short reviews with the category 'no word' (which we will label `0`) and truncate long reviews.

### (TODO) Create a word dictionary

To begin with, we need to construct a way to map words that appear in the reviews to integers. Here we fix the size of our vocabulary (including the 'no word' and 'infrequent' categories) to be `5000` but you may wish to change this to see how it affects the model.

> **TODO:** Complete the implementation for the `build_dict()` method below. Note that even though the vocab_size is set to `5000`, we only want to construct a mapping for the most frequently appearing `4998` words. This is because we want to reserve the special labels `0` for 'no word' and `1` for 'infrequent word'.

In [51]:
!pip install tqdm
from tqdm import tqdm
#Monitor the for loop like this [review_to_words(review) for review in tqdm(data_train)]

fastai 1.0.60 requires nvidia-ml-py3, which is not installed.
You are using pip version 10.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [86]:
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
word_dict = None
def build_dict(data, vocab_size = 5000):
    
    """vectorizer = CountVectorizer(max_features=vocabulary_size)
    features_train = vectorizer.fit_transform(words_train).toarray()

        # Apply the same vectorizer to transform the test documents (ignore unknown words)
        
        
        # NOTE: Remember to convert the features using .toarray() for a compact representation
        
        # Write to cache file for future runs (store vocabulary as well)
    vocabulary = vectorizer.vocabulary_"""
    
    """Construct and return a dictionary mapping each of the most frequently appearing words to a unique integer."""
    
    # TODO: Determine how often each word appears in `data`. Note that `data` is a list of sentences and that a
    #       sentence is a list of words.
    #print(set(tuple(x) for x in data))
    #flat_list = [item for sublist in data for item in sublist]
    #print(len(flat_list),len(set(flat_list)))
    print("flatten the list")
    flat_list = [item for sublist in tqdm(data) for item in sublist]
    """itr=0
    for sublist in data:
        for item in sublist:
            unique_data.append(item)
        itr+=1
        print("sentence # ",itr)"""
    print("len flat_list: ",len(flat_list))
    unique_data = list(set(flat_list))
    print("len set unique data: ",len(unique_data))#[x for x in set(data)] #tuple(x) for x in data)]
    #word_count = {} # A dict storing the words that appear in the reviews along with how often they occur
    print("word frequancies: ")
    wordfreq = [flat_list.count(p) for p in tqdm(unique_data)]
    print("max word freq:", max(wordfreq))
    word_count = {}
    #for p in tqdm(unique_data:
        #word_count.append()
    #print(unique_data,wordfreq)
    print("zip pairs of words with frequencies")
    word_count = dict(zip(unique_data,wordfreq))
    #unique_data,wordfreq = None
    # TODO: Sort the words found in `data` so that sorted_words[0] is the most frequently appearing word and
    #       sorted_words[-1] is the least frequently appearing word.
    sorted_words = []
    listofTuples = sorted(word_count.items() , reverse=True, key=lambda x: x[1])
    # Iterate over the sorted sequence
    for elem in listofTuples :
        print(elem[0] , " ::" , elem[1] )
    #itr=0
    sorted_words = [elem[0] for elem in listofTuples]#[(word_count[key], key) for key in tqdm(word_count)]
    print("word counts with keys")
    #for key in tqdm(word_count):
        #sorted_words.append((word_count[key], key))
        #print(itr)
        #itr+=1
    #sorted_words = aux
    #sorted_words.sort()
    #sorted_words.reverse()
    print(sorted_words)
    #sorted_words = aux
    print("dict: ")
    word_dict = {} # This is what we are building, a dictionary that translates words into integers
    for idx, word in tqdm(enumerate(sorted_words[:vocab_size - 2])): # The -2 is so that we save room for the 'no word'
        word_dict[word] = idx + 2       
        #print(idx)# 'infrequent' labels
        
    return word_dict

In [90]:
%%time
word_dict = build_dict(train_X)



  0%|          | 0/25000 [00:00<?, ?it/s]

100%|██████████| 25000/25000 [00:00<00:00, 231641.45it/s]

flatten the list
len flat_list:  3025130





  0%|          | 0/51857 [00:00<?, ?it/s]

  0%|          | 2/51857 [00:00<43:32, 19.85it/s]



len set unique data:  51857
word frequancies: 


  0%|          | 4/51857 [00:00<44:16, 19.52it/s]

  0%|          | 6/51857 [00:00<44:32, 19.40it/s]

  0%|          | 8/51857 [00:00<45:26, 19.02it/s]

  0%|          | 10/51857 [00:00<45:41, 18.91it/s]

  0%|          | 12/51857 [00:00<45:44, 18.89it/s]

  0%|          | 14/51857 [00:00<46:06, 18.74it/s]

  0%|          | 16/51857 [00:00<46:41, 18.50it/s]

  0%|          | 18/51857 [00:00<46:49, 18.45it/s]

  0%|          | 20/51857 [00:01<47:15, 18.28it/s]

  0%|          | 22/51857 [00:01<46:40, 18.51it/s]

  0%|          | 24/51857 [00:01<45:51, 18.84it/s]

  0%|          | 26/51857 [00:01<46:06, 18.73it/s]

  0%|          | 28/51857 [00:01<46:06, 18.73it/s]

  0%|          | 30/51857 [00:01<45:43, 18.89it/s]

  0%|          | 32/51857 [00:01<45:39, 18.92it/s]

  0%|          | 34/51857 [00:01<46:22, 18.62it/s]

  0%|          | 36/51857 [00:01<45:33, 18.96it/s]

  0%|          | 38/51857 [00:02<45:28, 18.99it/s]

  0%|          | 40/51857 [00:02<45:08, 19.13it/s]

  0%|          

...

tl  :: 1
pulcheri  :: 1
moldiest  :: 1
hazenut  :: 1
expectkey  :: 1
mckimson  :: 1
wholeheart  :: 1
approxiamt  :: 1
dirig  :: 1
amazingi  :: 1
funfair  :: 1
kilner  :: 1
coster  :: 1
secondsthrough  :: 1
sbardellati  :: 1
melisa  :: 1
heinkel  :: 1
bazeley  :: 1
eitel  :: 1
adi  :: 1
senki  :: 1
unbelivebl  :: 1
interpretaion  :: 1
crematorium  :: 1
prevar  :: 1
boylen  :: 1
keshu  :: 1
azghar  :: 1
lindey  :: 1
dooooooooooom  :: 1
rj  :: 1
drosselmei  :: 1
emptiest  :: 1
foolight  :: 1
unreconstruct  :: 1
lyndsay  :: 1
gyppo  :: 1
shatta  :: 1
carlottai  :: 1
reaccount  :: 1
woosh  :: 1
everbodi  :: 1
momosel  :: 1
addio  :: 1
judmila  :: 1
hob  :: 1
snarli  :: 1
hildi  :: 1
90c  :: 1
spasitc  :: 1
disinvit  :: 1
heeeeer  :: 1
deull  :: 1
approxi  :: 1
jaayen  :: 1
ceeb  :: 1
yurek  :: 1
foulata  :: 1
hellrid  :: 1
wpix  :: 1
pirro  :: 1
cinefest  :: 1
sinni  :: 1
huntsman  :: 1
glans  :: 1
blueberri  :: 1
radtha  :: 1
opp  :: 1
vedma  :: 1
enjoyth  :: 1
issei  :: 1
crapulast  :: 1


infinnerti  :: 1
pimpli  :: 1
somet  :: 1
litman  :: 1
dethaw  :: 1
wessel  :: 1
couldrel  :: 1
catatonia  :: 1
adagio  :: 1
yeeshhhhhhhhhhhhhhhhh  :: 1
lenser  :: 1
astrodom  :: 1
pakeeza  :: 1
fectli  :: 1
moonston  :: 1
katzenjamm  :: 1
bakhtyari  :: 1
esmerelda  :: 1
neema  :: 1
houseth  :: 1
vishq  :: 1
bib  :: 1
caall  :: 1
torrebruna  :: 1
takiya  :: 1
himmesh  :: 1
cavepeopl  :: 1
furtado  :: 1
abandonof  :: 1
spectecular  :: 1
speedskat  :: 1
lavin  :: 1
skyway  :: 1
motori  :: 1
mastantonio  :: 1
inerest  :: 1
teruyo  :: 1
hulbert  :: 1
maillard  :: 1
hulya  :: 1
avin  :: 1
enjoyeddavid  :: 1
hoopin  :: 1
mabi  :: 1
superwonderscop  :: 1
cill  :: 1
nuy  :: 1
colleh  :: 1
mig  :: 1
batperson  :: 1
bachstag  :: 1
salvif  :: 1
behl  :: 1
maypo  :: 1
blogg  :: 1
podgi  :: 1
queeg  :: 1
eeeee  :: 1
seawe  :: 1
slowmo  :: 1
475  :: 1
trist  :: 1
tuo  :: 1
7day  :: 1
grat  :: 1
londonscap  :: 1
amistad  :: 1
dawood  :: 1
aboutth  :: 1
playin  :: 1
reaaaal  :: 1
unact  :: 1
tarkoski 


familymemb  :: 1
desca  :: 1
meoli  :: 1
stoogephil  :: 1
dvorian  :: 1
saat  :: 1
potbelli  :: 1
blehfun  :: 1
manley  :: 1
superbug  :: 1
bloodwat  :: 1
virgini  :: 1
nlthe  :: 1
aufschnait  :: 1
ullal  :: 1
garza  :: 1
qe  :: 1
delattr  :: 1
salmi  :: 1
unsensation  :: 1
rocqu  :: 1
dima  :: 1
loust  :: 1
innacuraci  :: 1
hollandish  :: 1
gahagan  :: 1
kilkenni  :: 1
haaaaaaaa  :: 1
coreen  :: 1
bl  :: 1
childbear  :: 1
grimstead  :: 1
schmoeller  :: 1
hogwart  :: 1
unalter  :: 1
striper  :: 1
hollyood  :: 1
flamb  :: 1
ranier  :: 1
vlkava  :: 1
ahahahahahhahahahahahahahahahhahahahahahahah  :: 1
rereleas  :: 1
royl  :: 1
coxsuck  :: 1
billington  :: 1
unanticip  :: 1
heber  :: 1
6ey  :: 1
apoliceman  :: 1
timento  :: 1
libber  :: 1
kayl  :: 1
gondola  :: 1
keoma  :: 1
sivajiganeshan  :: 1
hausman  :: 1
msft3000  :: 1
deacon  :: 1
tweaker  :: 1
gitwist  :: 1
inborn  :: 1
reissuer  :: 1
udon  :: 1
esssenc  :: 1
iedereen  :: 1
hjerner  :: 1
spririt  :: 1
freebas  :: 1
mamer  :: 1
heme

4998it [00:00, 425811.61it/s]

CPU times: user 47min 50s, sys: 15.8 s, total: 48min 6s
Wall time: 48min 4s


In [95]:
#word_dict
    
listofTuples = sorted(word_dict.items() , key=lambda x: x[1])
 
# Iterate over the sorted sequence
for elem in listofTuples :
    print(elem[0] , " ::" , elem[1] )

movi  :: 2
film  :: 3
one  :: 4
like  :: 5
time  :: 6
good  :: 7
make  :: 8
charact  :: 9
get  :: 10
see  :: 11
watch  :: 12
stori  :: 13
even  :: 14
would  :: 15
realli  :: 16
well  :: 17
scene  :: 18
look  :: 19
show  :: 20
much  :: 21
end  :: 22
peopl  :: 23
bad  :: 24
go  :: 25
great  :: 26
also  :: 27
first  :: 28
love  :: 29
think  :: 30
way  :: 31
act  :: 32
play  :: 33
made  :: 34
thing  :: 35
could  :: 36
know  :: 37
say  :: 38
seem  :: 39
work  :: 40
plot  :: 41
two  :: 42
actor  :: 43
year  :: 44
come  :: 45
mani  :: 46
seen  :: 47
take  :: 48
life  :: 49
want  :: 50
never  :: 51
littl  :: 52
best  :: 53
tri  :: 54
man  :: 55
ever  :: 56
give  :: 57
better  :: 58
still  :: 59
perform  :: 60
find  :: 61
feel  :: 62
part  :: 63
back  :: 64
use  :: 65
someth  :: 66
director  :: 67
actual  :: 68
interest  :: 69
lot  :: 70
real  :: 71
old  :: 72
cast  :: 73
though  :: 74
live  :: 75
star  :: 76
enjoy  :: 77
guy  :: 78
anoth  :: 79
new  :: 80
role  :: 81
noth  :: 82
10  :: 83
funn

mark  :: 671
red  :: 672
dull  :: 673
adapt  :: 674
within  :: 675
lose  :: 676
spend  :: 677
color  :: 678
materi  :: 679
chase  :: 680
mari  :: 681
storylin  :: 682
forget  :: 683
bunch  :: 684
clear  :: 685
lee  :: 686
victim  :: 687
nearli  :: 688
box  :: 689
york  :: 690
match  :: 691
inspir  :: 692
mess  :: 693
finish  :: 694
standard  :: 695
easi  :: 696
truth  :: 697
suffer  :: 698
busi  :: 699
bill  :: 700
space  :: 701
dramat  :: 702
western  :: 703
e  :: 704
list  :: 705
battl  :: 706
notic  :: 707
de  :: 708
french  :: 709
ad  :: 710
9  :: 711
tom  :: 712
larg  :: 713
among  :: 714
eventu  :: 715
accept  :: 716
train  :: 717
agre  :: 718
spirit  :: 719
soundtrack  :: 720
third  :: 721
teenag  :: 722
soldier  :: 723
adventur  :: 724
sorri  :: 725
famou  :: 726
suggest  :: 727
drug  :: 728
normal  :: 729
cri  :: 730
babi  :: 731
ultim  :: 732
troubl  :: 733
contain  :: 734
certain  :: 735
cultur  :: 736
romanc  :: 737
rare  :: 738
lame  :: 739
somehow  :: 740
mix  :: 741
disn

bed  :: 1256
central  :: 1257
content  :: 1258
iron  :: 1259
sell  :: 1260
everybodi  :: 1261
gag  :: 1262
hotel  :: 1263
slowli  :: 1264
hire  :: 1265
system  :: 1266
charl  :: 1267
individu  :: 1268
hey  :: 1269
adam  :: 1270
thrown  :: 1271
mediocr  :: 1272
allen  :: 1273
jone  :: 1274
lesson  :: 1275
ray  :: 1276
billi  :: 1277
cameo  :: 1278
photographi  :: 1279
pari  :: 1280
fellow  :: 1281
strike  :: 1282
brief  :: 1283
rise  :: 1284
independ  :: 1285
absurd  :: 1286
neg  :: 1287
phone  :: 1288
impact  :: 1289
model  :: 1290
ill  :: 1291
born  :: 1292
spoil  :: 1293
fresh  :: 1294
angl  :: 1295
likabl  :: 1296
abus  :: 1297
discuss  :: 1298
hill  :: 1299
sight  :: 1300
ahead  :: 1301
sent  :: 1302
photograph  :: 1303
occur  :: 1304
blame  :: 1305
shine  :: 1306
logic  :: 1307
bruce  :: 1308
mainli  :: 1309
commerci  :: 1310
forev  :: 1311
skip  :: 1312
segment  :: 1313
surround  :: 1314
teacher  :: 1315
held  :: 1316
blond  :: 1317
zero  :: 1318
trap  :: 1319
summer  :: 1320
res

awkward  :: 1797
speech  :: 1798
13  :: 1799
sean  :: 1800
psycho  :: 1801
anthoni  :: 1802
clip  :: 1803
corni  :: 1804
priest  :: 1805
curiou  :: 1806
advic  :: 1807
theatric  :: 1808
w  :: 1809
reli  :: 1810
religion  :: 1811
flow  :: 1812
addict  :: 1813
asian  :: 1814
skin  :: 1815
howard  :: 1816
specif  :: 1817
secur  :: 1818
jennif  :: 1819
core  :: 1820
organ  :: 1821
comfort  :: 1822
golden  :: 1823
luke  :: 1824
promot  :: 1825
lucki  :: 1826
cheat  :: 1827
cash  :: 1828
dislik  :: 1829
associ  :: 1830
lower  :: 1831
wing  :: 1832
degre  :: 1833
contribut  :: 1834
spell  :: 1835
frequent  :: 1836
balanc  :: 1837
frankli  :: 1838
devic  :: 1839
regret  :: 1840
lake  :: 1841
forgiv  :: 1842
print  :: 1843
sake  :: 1844
thoma  :: 1845
betti  :: 1846
mass  :: 1847
crack  :: 1848
unexpect  :: 1849
gordon  :: 1850
categori  :: 1851
invit  :: 1852
grown  :: 1853
depend  :: 1854
construct  :: 1855
amateur  :: 1856
unfold  :: 1857
matur  :: 1858
honor  :: 1859
walter  :: 1860
intelle

puppet  :: 2780
resort  :: 2781
tool  :: 2782
phillip  :: 2783
choreograph  :: 2784
guilt  :: 2785
pig  :: 2786
muppet  :: 2787
tribut  :: 2788
basement  :: 2789
boll  :: 2790
exercis  :: 2791
cruis  :: 2792
puzzl  :: 2793
medium  :: 2794
document  :: 2795
tower  :: 2796
scarecrow  :: 2797
stan  :: 2798
editor  :: 2799
ham  :: 2800
fianc  :: 2801
korean  :: 2802
layer  :: 2803
babe  :: 2804
toilet  :: 2805
item  :: 2806
slip  :: 2807
ward  :: 2808
24  :: 2809
file  :: 2810
portion  :: 2811
philosoph  :: 2812
inexplic  :: 2813
assur  :: 2814
slaughter  :: 2815
doc  :: 2816
persona  :: 2817
orient  :: 2818
catherin  :: 2819
librari  :: 2820
denzel  :: 2821
minim  :: 2822
glover  :: 2823
larger  :: 2824
transit  :: 2825
territori  :: 2826
superfici  :: 2827
spark  :: 2828
jeremi  :: 2829
pg  :: 2830
ban  :: 2831
curti  :: 2832
owe  :: 2833
jet  :: 2834
wolf  :: 2835
financi  :: 2836
walken  :: 2837
boredom  :: 2838
sneak  :: 2839
shi  :: 2840
dorothi  :: 2841
metaphor  :: 2842
profound  :

ginger  :: 3418
hbo  :: 3419
assembl  :: 3420
leon  :: 3421
harvey  :: 3422
apolog  :: 3423
milk  :: 3424
sore  :: 3425
interrupt  :: 3426
undoubtedli  :: 3427
olivi  :: 3428
equip  :: 3429
coat  :: 3430
pant  :: 3431
promin  :: 3432
chest  :: 3433
inappropri  :: 3434
tribe  :: 3435
1996  :: 3436
coffe  :: 3437
gear  :: 3438
polanski  :: 3439
retain  :: 3440
exot  :: 3441
primari  :: 3442
furthermor  :: 3443
trace  :: 3444
instant  :: 3445
airplan  :: 3446
devast  :: 3447
brooklyn  :: 3448
highest  :: 3449
institut  :: 3450
jenni  :: 3451
colleagu  :: 3452
aveng  :: 3453
pen  :: 3454
pot  :: 3455
humbl  :: 3456
colonel  :: 3457
embrac  :: 3458
maggi  :: 3459
vulgar  :: 3460
florida  :: 3461
consum  :: 3462
solut  :: 3463
gender  :: 3464
dian  :: 3465
poke  :: 3466
rick  :: 3467
dutch  :: 3468
1999  :: 3469
wive  :: 3470
cope  :: 3471
strain  :: 3472
smaller  :: 3473
outer  :: 3474
ya  :: 3475
bowl  :: 3476
3rd  :: 3477
principl  :: 3478
disabl  :: 3479
linda  :: 3480
godzilla  :: 3481


sailor  :: 3944
proce  :: 3945
unorigin  :: 3946
attribut  :: 3947
inher  :: 3948
keith  :: 3949
prey  :: 3950
analysi  :: 3951
pink  :: 3952
nineti  :: 3953
interior  :: 3954
incorpor  :: 3955
approv  :: 3956
boxer  :: 3957
barrymor  :: 3958
ridden  :: 3959
emphas  :: 3960
unrel  :: 3961
meg  :: 3962
drift  :: 3963
carla  :: 3964
improvis  :: 3965
fleet  :: 3966
degrad  :: 3967
bunni  :: 3968
mighti  :: 3969
simmon  :: 3970
belushi  :: 3971
hypnot  :: 3972
mormon  :: 3973
millionair  :: 3974
othello  :: 3975
julian  :: 3976
walsh  :: 3977
elm  :: 3978
meyer  :: 3979
underli  :: 3980
robbin  :: 3981
er  :: 3982
condemn  :: 3983
substitut  :: 3984
stalker  :: 3985
nicol  :: 3986
indiffer  :: 3987
undeni  :: 3988
barrel  :: 3989
predat  :: 3990
priceless  :: 3991
mtv  :: 3992
hay  :: 3993
disord  :: 3994
dolph  :: 3995
novak  :: 3996
alison  :: 3997
agenda  :: 3998
edgi  :: 3999
alarm  :: 4000
warmth  :: 4001
exquisit  :: 4002
firm  :: 4003
errol  :: 4004
roof  :: 4005
lampoon  :: 4006
e

mermaid  :: 4523
angst  :: 4524
biker  :: 4525
candl  :: 4526
dandi  :: 4527
enlist  :: 4528
tick  :: 4529
sooner  :: 4530
taboo  :: 4531
injur  :: 4532
harmless  :: 4533
viewpoint  :: 4534
renaiss  :: 4535
suprem  :: 4536
preachi  :: 4537
outlaw  :: 4538
headach  :: 4539
virtu  :: 4540
uh  :: 4541
73  :: 4542
contempt  :: 4543
glorifi  :: 4544
gere  :: 4545
foolish  :: 4546
phenomenon  :: 4547
macho  :: 4548
tripl  :: 4549
immatur  :: 4550
stimul  :: 4551
corbett  :: 4552
camcord  :: 4553
intric  :: 4554
idol  :: 4555
amor  :: 4556
whore  :: 4557
overlong  :: 4558
filth  :: 4559
spade  :: 4560
bent  :: 4561
dismal  :: 4562
dish  :: 4563
boston  :: 4564
surgeri  :: 4565
scorses  :: 4566
claustrophob  :: 4567
steer  :: 4568
sox  :: 4569
hostag  :: 4570
cassavet  :: 4571
zoom  :: 4572
ariel  :: 4573
stair  :: 4574
slimi  :: 4575
ebert  :: 4576
hooker  :: 4577
fluff  :: 4578
redund  :: 4579
hokey  :: 4580
guin  :: 4581
oldest  :: 4582
salt  :: 4583
messi  :: 4584
cush  :: 4585
proport  ::

In [94]:
len(word_dict)

4998

**Question:** What are the five most frequently appearing (tokenized) words in the training set? Does it makes sense that these words appear frequently in the training set?

**Answer:** movi, film, one, like, time

##### TODO: Use this space to determine the five most frequently appearing words in the training set.

In [93]:
i=0
for wd in word_dict:
    print(wd)
    i+=1
    if i==5:
        break

movi
film
one
like
time


### Save `word_dict`

Later on when we construct an endpoint which processes a submitted review we will need to make use of the `word_dict` which we have created. As such, we will save it to a file now for future use.

In [91]:
data_dir = '../data/pytorch' # The folder we will use for storing data
if not os.path.exists(data_dir): # Make sure that the folder exists
    os.makedirs(data_dir)

In [92]:
with open(os.path.join(data_dir, 'word_dict.pkl'), "wb") as f:
    pickle.dump(word_dict, f)

### Transform the reviews

Now that we have our word dictionary which allows us to transform the words appearing in the reviews into integers, it is time to make use of it and convert our reviews to their integer sequence representation, making sure to pad or truncate to a fixed length, which in our case is `500`.

In [96]:
def convert_and_pad(word_dict, sentence, pad=500):
    NOWORD = 0 # We will use 0 to represent the 'no word' category
    INFREQ = 1 # and we use 1 to represent the infrequent words, i.e., words not appearing in word_dict
    
    working_sentence = [NOWORD] * pad
    
    for word_index, word in enumerate(sentence[:pad]):
        if word in word_dict:
            working_sentence[word_index] = word_dict[word]
        else:
            working_sentence[word_index] = INFREQ
            
    return working_sentence, min(len(sentence), pad)

def convert_and_pad_data(word_dict, data, pad=500):
    result = []
    lengths = []
    
    for sentence in data:
        converted, leng = convert_and_pad(word_dict, sentence, pad)
        result.append(converted)
        lengths.append(leng)
        
    return np.array(result), np.array(lengths)

In [97]:
train_X, train_X_len = convert_and_pad_data(word_dict, train_X)
test_X, test_X_len = convert_and_pad_data(word_dict, test_X)

As a quick check to make sure that things are working as intended, check to see what one of the reviews in the training set looks like after having been processeed. Does this look reasonable? What is the length of a review in the training set?

In [98]:
# Use this cell to examine one of the processed reviews to make sure everything is working as intended.
print(len(train_X[1]),train_X_len)
train_X[1]

500 [ 79 210 113 ... 156  60  46]


array([ 487,    3,   98,    1,  686,   34,  142,   11,    1,   67, 2954,
       1739, 1480,    1,  890, 1339,   55,  162,   44,  536,  195,  196,
       2743, 1606, 2347,   95,  591,   79,  183, 2261, 1753,  199,   13,
         48,  145,    1, 2853,  513, 2397, 2059,   51, 2320, 1352,    1,
       1116,  235,  586, 4538,  879,  167,    1, 1862,  924,  114,  434,
         15,    1, 2853, 3204, 3662, 1641, 1070,    2,  840,  844, 4515,
        238,  362,    6, 1392, 2917, 1608,  103,    1, 3606, 1676, 2853,
         76,    2,  830,  353, 4149, 1425,   17,   73,  107,    1, 2215,
         76,    1,    1,   73,  107,  899, 2992,  237,    1,    1,  899,
        278, 2853, 3595,  107,   55,  222,   43,  312, 1294,  214, 1396,
        568,   60,    1,  108, 1199,  420, 1944,  102,  199, 3403,    1,
          1, 2450,  941,    1, 3931,  107,   55, 1155, 1875,   57,  410,
       3842,   60,   32,  115, 1495,  187,  114, 1412,  844,  818,   80,
       2397, 4071,  430,  946, 1735, 3352,  572,  3

**Question:** In the cells above we use the `preprocess_data` and `convert_and_pad_data` methods to process both the training and testing set. Why or why not might this be a problem?

**Answer:**
the current implementation of `preprocess_data` method requires 2 labeled sets, it doesn't allow to preprocess and dump train, val, test sets at the same time. Also, preprocessing of a new unlabled test set would raise an error.
`convert_and_pad_data` doesn't cause any problems since we assume that both sets are in the same domain (therefore the words come from one dictionary), and if the test set has any words not present in train set, these words will get the key `1`.

## Step 3: Upload the data to S3

As in the XGBoost notebook, we will need to upload the training dataset to S3 in order for our training code to access it. For now we will save it locally and we will upload to S3 later on.

### Save the processed training dataset locally

It is important to note the format of the data that we are saving as we will need to know it when we write the training code. In our case, each row of the dataset has the form `label`, `length`, `review[500]` where `review[500]` is a sequence of `500` integers representing the words in the review.

In [99]:
import pandas as pd
    
pd.concat([pd.DataFrame(train_y), pd.DataFrame(train_X_len), pd.DataFrame(train_X)], axis=1) \
        .to_csv(os.path.join(data_dir, 'train.csv'), header=False, index=False)

### Uploading the training data


Next, we need to upload the training data to the SageMaker default S3 bucket so that we can provide access to it while training our model.

In [100]:
import sagemaker

sagemaker_session = sagemaker.Session()

bucket = sagemaker_session.default_bucket()
prefix = 'sagemaker/sentiment_rnn'

role = sagemaker.get_execution_role()

In [101]:
input_data = sagemaker_session.upload_data(path=data_dir, bucket=bucket, key_prefix=prefix)

**NOTE:** The cell above uploads the entire contents of our data directory. This includes the `word_dict.pkl` file. This is fortunate as we will need this later on when we create an endpoint that accepts an arbitrary review. For now, we will just take note of the fact that it resides in the data directory (and so also in the S3 training bucket) and that we will need to make sure it gets saved in the model directory.

## Step 4: Build and Train the PyTorch Model

In the XGBoost notebook we discussed what a model is in the SageMaker framework. In particular, a model comprises three objects

 - Model Artifacts,
 - Training Code, and
 - Inference Code,
 
each of which interact with one another. In the XGBoost example we used training and inference code that was provided by Amazon. Here we will still be using containers provided by Amazon with the added benefit of being able to include our own custom code.

We will start by implementing our own neural network in PyTorch along with a training script. For the purposes of this project we have provided the necessary model object in the `model.py` file, inside of the `train` folder. You can see the provided implementation by running the cell below.

In [22]:
!pygmentize train/model.py

import torch.nn as nn

class LSTMClassifier(nn.Module):
    """
    This is the simple RNN model we will be using to perform Sentiment Analysis.
    """

    def __init__(self, embedding_dim, hidden_dim, vocab_size):
        """
        Initialize the model by settingg up the various layers.
        """
        super(LSTMClassifier, self).__init__()

        self.embedding = nn.Embedding(vocab_size, embedding_dim, padding_idx=0)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim)
        self.dense = nn.Linear(in_features=hidden_dim, out_features=1)
        self.sig = nn.Sigmoid()
        
        self.word_dict = None

    def forward(self, x):
        """
        Perform a forward pass of our model on some input.
        """
        x = x.t()
        lengths = x[0,:]
        reviews = x[1:,:]
        embeds = self.embedding(reviews)
        lstm_out, _ = self.lstm(embeds)
        out = self.dense(lstm_out)
        out = out[lengths - 1, range(len(lengths))]
        return self.sig

The important takeaway from the implementation provided is that there are three parameters that we may wish to tweak to improve the performance of our model. These are the embedding dimension, the hidden dimension and the size of the vocabulary. We will likely want to make these parameters configurable in the training script so that if we wish to modify them we do not need to modify the script itself. We will see how to do this later on. To start we will write some of the training code in the notebook so that we can more easily diagnose any issues that arise.

First we will load a small portion of the training data set to use as a sample. It would be very time consuming to try and train the model completely in the notebook as we do not have access to a gpu and the compute instance that we are using is not particularly powerful. However, we can work on a small bit of the data to get a feel for how our training script is behaving.

In [102]:
import torch
import torch.utils.data

# Read in only the first 250 rows
train_sample = pd.read_csv(os.path.join(data_dir, 'train.csv'), header=None, names=None, nrows=250)

# Turn the input pandas dataframe into tensors
train_sample_y = torch.from_numpy(train_sample[[0]].values).float().squeeze()
train_sample_X = torch.from_numpy(train_sample.drop([0], axis=1).values).long()

# Build the dataset
train_sample_ds = torch.utils.data.TensorDataset(train_sample_X, train_sample_y)
# Build the dataloader
train_sample_dl = torch.utils.data.DataLoader(train_sample_ds, batch_size=50)

### (TODO) Writing the training method

Next we need to write the training code itself. This should be very similar to training methods that you have written before to train PyTorch models. We will leave any difficult aspects such as model saving / loading and parameter loading until a little later.

In [117]:
def train(model, train_loader, epochs, optimizer, loss_fn, device):
    for epoch in range(1, epochs + 1):
        model.train()
        total_loss = 0
        for batch in train_loader:         
            batch_X, batch_y = batch
            
            batch_X = batch_X.to(device)
            batch_y = batch_y.to(device)
            
            # TODO: Complete this train method to train the model provided.
            #x, y = place_and_unwrap(batch, device)
            with torch.set_grad_enabled(True):
             
                out = model(batch_X)
                    
                loss = loss_fn(out, batch_y)

            #if is_training:
            optimizer.zero_grad()
                  
            loss.backward()
               
            optimizer.step()

            #phase.batch_loss = loss.item()
            #
            total_loss += loss.data.item()
        print("Epoch: {}, BCELoss: {}".format(epoch, total_loss / len(train_loader)))

Supposing we have the training method above, we will test that it is working by writing a bit of code in the notebook that executes our training method on the small sample training set that we loaded earlier. The reason for doing this in the notebook is so that we have an opportunity to fix any errors that arise early when they are easier to diagnose.

In [118]:
import torch.optim as optim
from train.model import LSTMClassifier

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = LSTMClassifier(32, 100, 5000).to(device)
optimizer = optim.Adam(model.parameters())
loss_fn = torch.nn.BCELoss()

train(model, train_sample_dl, 1, optimizer, loss_fn, device)

Epoch: 1, BCELoss: 0.6923759818077088


In order to construct a PyTorch model using SageMaker we must provide SageMaker with a training script. We may optionally include a directory which will be copied to the container and from which our training code will be run. When the training container is executed it will check the uploaded directory (if there is one) for a `requirements.txt` file and install any required Python libraries, after which the training script will be run.

### (TODO) Training the model

When a PyTorch model is constructed in SageMaker, an entry point must be specified. This is the Python file which will be executed when the model is trained. Inside of the `train` directory is a file called `train.py` which has been provided and which contains most of the necessary code to train our model. The only thing that is missing is the implementation of the `train()` method which you wrote earlier in this notebook.

**TODO**: Copy the `train()` method written above and paste it into the `train/train.py` file where required.

The way that SageMaker passes hyperparameters to the training script is by way of arguments. These arguments can then be parsed and used in the training script. To see how this is done take a look at the provided `train/train.py` file.

In [107]:
from sagemaker.pytorch import PyTorch

estimator = PyTorch(entry_point="train.py",
                    source_dir="train",
                    role=role,
                    framework_version='0.4.0',
                    train_instance_count=4,
                    train_instance_type= 'ml.m4.xlarge',#'ml.p2.xlarge',
                    hyperparameters={
                        'epochs': 10,
                        'hidden_dim': 200,
                    })

In [108]:
estimator.fit({'training': input_data})

2020-04-04 22:20:52 Starting - Starting the training job...
2020-04-04 22:20:53 Starting - Launching requested ML instances......
2020-04-04 22:21:56 Starting - Preparing the instances for training......
2020-04-04 22:23:14 Downloading - Downloading input data......
2020-04-04 22:24:05 Training - Downloading the training image.bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2020-04-04 22:24:25,297 sagemaker-containers INFO     Imported framework sagemaker_pytorch_container.training
2020-04-04 22:24:25,299 sagemaker-containers INFO     No GPUs detected (normal if no gpus installed)
2020-04-04 22:24:25,313 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2020-04-04 22:24:25,457 sagemaker-containers INFO     Imported framework sagemaker_pytorch_container.training
2020-04-04 22:


2020-04-04 22:24:25 Training - Training image download completed. Training in progress.Successfully installed beautifulsoup4-4.8.2 html5lib-1.0.1 nltk-3.4.5 numpy-1.18.2 pandas-0.24.2 pytz-2019.3 soupsieve-2.0 train-1.0.0 webencodings-0.5.1
You are using pip version 18.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
2020-04-04 22:24:39,107 sagemaker-containers INFO     No GPUs detected (normal if no gpus installed)
2020-04-04 22:24:39,121 sagemaker-containers INFO     Invoking user script

Training Env:

{
    "input_data_config": {
        "training": {
            "TrainingInputMode": "File",
            "S3DistributionType": "FullyReplicated",
            "RecordWrapperType": "None"
        }
    },
    "user_entry_point": "train.py",
    "output_data_dir": "/opt/ml/output/data",
    "output_dir": "/opt/ml/output",
    "additional_framework_parameters": {},
    "input_dir": "/opt/ml/input",
    "current_host": "algo

KeyboardInterrupt: 

In [ ]:
estimator.

## Step 5: Testing the model

As mentioned at the top of this notebook, we will be testing this model by first deploying it and then sending the testing data to the deployed endpoint. We will do this so that we can make sure that the deployed model is working correctly.

## Step 6: Deploy the model for testing

Now that we have trained our model, we would like to test it to see how it performs. Currently our model takes input of the form `review_length, review[500]` where `review[500]` is a sequence of `500` integers which describe the words present in the review, encoded using `word_dict`. Fortunately for us, SageMaker provides built-in inference code for models with simple inputs such as this.

There is one thing that we need to provide, however, and that is a function which loads the saved model. This function must be called `model_fn()` and takes as its only parameter a path to the directory where the model artifacts are stored. This function must also be present in the python file which we specified as the entry point. In our case the model loading function has been provided and so no changes need to be made.

**NOTE**: When the built-in inference code is run it must import the `model_fn()` method from the `train.py` file. This is why the training code is wrapped in a main guard ( ie, `if __name__ == '__main__':` )

Since we don't need to change anything in the code that was uploaded during training, we can simply deploy the current model as-is.

**NOTE:** When deploying a model you are asking SageMaker to launch an compute instance that will wait for data to be sent to it. As a result, this compute instance will continue to run until *you* shut it down. This is important to know since the cost of a deployed endpoint depends on how long it has been running for.

In other words **If you are no longer using a deployed endpoint, shut it down!**

**TODO:** Deploy the trained model.

In [112]:
# TODO: Deploy the trained model
predictor = estimator.deploy(initial_instance_count=1, instance_type='ml.m4.xlarge')

KeyError: 'ModelArtifacts'

## Step 7 - Use the model for testing

Once deployed, we can read in the test data and send it off to our deployed model to get some results. Once we collect all of the results we can determine how accurate our model is.

In [113]:
test_X = pd.concat([pd.DataFrame(test_X_len), pd.DataFrame(test_X)], axis=1)

In [122]:
# We split the data into chunks and send each chunk seperately, accumulating the results.

def predict(data, rows=512):
    split_array = np.array_split(data, int(data.shape[0] / float(rows) + 1))
    predictions = np.array([])
    for array in split_array:
        predictions = np.append(predictions, predictor.predict(array))
    
    return predictions

In [ ]:
model.

In [123]:
predictions = predict(test_X.values)
predictions = [round(num) for num in predictions]

AttributeError: 'numpy.ndarray' object has no attribute 't'

In [ ]:
from sklearn.metrics import accuracy_score
accuracy_score(test_y, predictions)

**Question:** How does this model compare to the XGBoost model you created earlier? Why might these two models perform differently on this dataset? Which do *you* think is better for sentiment analysis?

**Answer:**

### (TODO) More testing

We now have a trained model which has been deployed and which we can send processed reviews to and which returns the predicted sentiment. However, ultimately we would like to be able to send our model an unprocessed review. That is, we would like to send the review itself as a string. For example, suppose we wish to send the following review to our model.

In [110]:
test_review = 'The simplest pleasures in life are the best, and this film is one of them. Combining a rather basic storyline of love and adventure this movie transcends the usual weekend fair with wit and unmitigated charm.'

The question we now need to answer is, how do we send this review to our model?

Recall in the first section of this notebook we did a bunch of data processing to the IMDb dataset. In particular, we did two specific things to the provided reviews.
 - Removed any html tags and stemmed the input
 - Encoded the review as a sequence of integers using `word_dict`
 
In order process the review we will need to repeat these two steps.

**TODO**: Using the `review_to_words` and `convert_and_pad` methods from section one, convert `test_review` into a numpy array `test_data` suitable to send to our model. Remember that our model expects input of the form `review_length, review[500]`.

In [124]:
# TODO: Convert test_review into a form usable by the model and save the results in test_data
test_review_words = review_to_words(test_review)
print(len(test_review_words),test_review_words)
test_data,test_review_lenght = convert_and_pad(word_dict, test_review_words, pad=500)
print(test_data,test_review_lenght)

20 ['simplest', 'pleasur', 'life', 'best', 'film', 'one', 'combin', 'rather', 'basic', 'storylin', 'love', 'adventur', 'movi', 'transcend', 'usual', 'weekend', 'fair', 'wit', 'unmitig', 'charm']
[1, 1374, 49, 53, 3, 4, 878, 173, 392, 682, 29, 724, 2, 4431, 275, 2077, 1059, 760, 1, 582, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

Now that we have processed the review, we can send the resulting array to our model to predict the sentiment of the review.

In [ ]:
predictor.predict(test_data)

Since the return value of our model is close to `1`, we can be certain that the review we submitted is positive.

### Delete the endpoint

Of course, just like in the XGBoost notebook, once we've deployed an endpoint it continues to run until we tell it to shut down. Since we are done using our endpoint for now, we can delete it.

In [ ]:
estimator.delete_endpoint()

## Step 6 (again) - Deploy the model for the web app

Now that we know that our model is working, it's time to create some custom inference code so that we can send the model a review which has not been processed and have it determine the sentiment of the review.

As we saw above, by default the estimator which we created, when deployed, will use the entry script and directory which we provided when creating the model. However, since we now wish to accept a string as input and our model expects a processed review, we need to write some custom inference code.

We will store the code that we write in the `serve` directory. Provided in this directory is the `model.py` file that we used to construct our model, a `utils.py` file which contains the `review_to_words` and `convert_and_pad` pre-processing functions which we used during the initial data processing, and `predict.py`, the file which will contain our custom inference code. Note also that `requirements.txt` is present which will tell SageMaker what Python libraries are required by our custom inference code.

When deploying a PyTorch model in SageMaker, you are expected to provide four functions which the SageMaker inference container will use.
 - `model_fn`: This function is the same function that we used in the training script and it tells SageMaker how to load our model.
 - `input_fn`: This function receives the raw serialized input that has been sent to the model's endpoint and its job is to de-serialize and make the input available for the inference code.
 - `output_fn`: This function takes the output of the inference code and its job is to serialize this output and return it to the caller of the model's endpoint.
 - `predict_fn`: The heart of the inference script, this is where the actual prediction is done and is the function which you will need to complete.

For the simple website that we are constructing during this project, the `input_fn` and `output_fn` methods are relatively straightforward. We only require being able to accept a string as input and we expect to return a single value as output. You might imagine though that in a more complex application the input or output may be image data or some other binary data which would require some effort to serialize.

### (TODO) Writing inference code

Before writing our custom inference code, we will begin by taking a look at the code which has been provided.

In [ ]:
!pygmentize serve/predict.py

As mentioned earlier, the `model_fn` method is the same as the one provided in the training code and the `input_fn` and `output_fn` methods are very simple and your task will be to complete the `predict_fn` method. Make sure that you save the completed file as `predict.py` in the `serve` directory.

**TODO**: Complete the `predict_fn()` method in the `serve/predict.py` file.

### Deploying the model

Now that the custom inference code has been written, we will create and deploy our model. To begin with, we need to construct a new PyTorchModel object which points to the model artifacts created during training and also points to the inference code that we wish to use. Then we can call the deploy method to launch the deployment container.

**NOTE**: The default behaviour for a deployed PyTorch model is to assume that any input passed to the predictor is a `numpy` array. In our case we want to send a string so we need to construct a simple wrapper around the `RealTimePredictor` class to accomodate simple strings. In a more complicated situation you may want to provide a serialization object, for example if you wanted to sent image data.

In [125]:
from sagemaker.predictor import RealTimePredictor
from sagemaker.pytorch import PyTorchModel

class StringPredictor(RealTimePredictor):
    def __init__(self, endpoint_name, sagemaker_session):
        super(StringPredictor, self).__init__(endpoint_name, sagemaker_session, content_type='text/plain')

model = PyTorchModel(model_data=estimator.model_data,
                     role = role,
                     framework_version='0.4.0',
                     entry_point='predict.py',
                     source_dir='serve',
                     predictor_cls=StringPredictor)
predictor = model.deploy(initial_instance_count=1, instance_type='ml.m4.xlarge')

KeyError: 'ModelArtifacts'

### Testing the model

Now that we have deployed our model with the custom inference code, we should test to see if everything is working. Here we test our model by loading the first `250` positive and negative reviews and send them to the endpoint, then collect the results. The reason for only sending some of the data is that the amount of time it takes for our model to process the input and then perform inference is quite long and so testing the entire data set would be prohibitive.

In [126]:
import glob

def test_reviews(data_dir='../data/aclImdb', stop=250):
    
    results = []
    ground = []
    
    # We make sure to test both positive and negative reviews    
    for sentiment in ['pos', 'neg']:
        
        path = os.path.join(data_dir, 'test', sentiment, '*.txt')
        files = glob.glob(path)
        
        files_read = 0
        
        print('Starting ', sentiment, ' files')
        
        # Iterate through the files and send them to the predictor
        for f in files:
            with open(f) as review:
                # First, we store the ground truth (was the review positive or negative)
                if sentiment == 'pos':
                    ground.append(1)
                else:
                    ground.append(0)
                # Read in the review and convert to 'utf-8' for transmission via HTTP
                review_input = review.read().encode('utf-8')
                # Send the review to the predictor and store the results
                results.append(int(predictor.predict(review_input)))
                
            # Sending reviews to our endpoint one at a time takes a while so we
            # only send a small number of reviews
            files_read += 1
            if files_read == stop:
                break
            
    return ground, results

In [127]:
ground, results = test_reviews()

Starting  pos  files


AttributeError: 'LSTMClassifier' object has no attribute 'predict'

In [ ]:
from sklearn.metrics import accuracy_score
accuracy_score(ground, results)

As an additional test, we can try sending the `test_review` that we looked at earlier.

In [ ]:
predictor.predict(test_review)

Now that we know our endpoint is working as expected, we can set up the web page that will interact with it. If you don't have time to finish the project now, make sure to skip down to the end of this notebook and shut down your endpoint. You can deploy it again when you come back.

## Step 7 (again): Use the model for the web app

> **TODO:** This entire section and the next contain tasks for you to complete, mostly using the AWS console.

So far we have been accessing our model endpoint by constructing a predictor object which uses the endpoint and then just using the predictor object to perform inference. What if we wanted to create a web app which accessed our model? The way things are set up currently makes that not possible since in order to access a SageMaker endpoint the app would first have to authenticate with AWS using an IAM role which included access to SageMaker endpoints. However, there is an easier way! We just need to use some additional AWS services.

<img src="Web App Diagram.svg">

The diagram above gives an overview of how the various services will work together. On the far right is the model which we trained above and which is deployed using SageMaker. On the far left is our web app that collects a user's movie review, sends it off and expects a positive or negative sentiment in return.

In the middle is where some of the magic happens. We will construct a Lambda function, which you can think of as a straightforward Python function that can be executed whenever a specified event occurs. We will give this function permission to send and recieve data from a SageMaker endpoint.

Lastly, the method we will use to execute the Lambda function is a new endpoint that we will create using API Gateway. This endpoint will be a url that listens for data to be sent to it. Once it gets some data it will pass that data on to the Lambda function and then return whatever the Lambda function returns. Essentially it will act as an interface that lets our web app communicate with the Lambda function.

### Setting up a Lambda function

The first thing we are going to do is set up a Lambda function. This Lambda function will be executed whenever our public API has data sent to it. When it is executed it will receive the data, perform any sort of processing that is required, send the data (the review) to the SageMaker endpoint we've created and then return the result.

#### Part A: Create an IAM Role for the Lambda function

Since we want the Lambda function to call a SageMaker endpoint, we need to make sure that it has permission to do so. To do this, we will construct a role that we can later give the Lambda function.

Using the AWS Console, navigate to the **IAM** page and click on **Roles**. Then, click on **Create role**. Make sure that the **AWS service** is the type of trusted entity selected and choose **Lambda** as the service that will use this role, then click **Next: Permissions**.

In the search box type `sagemaker` and select the check box next to the **AmazonSageMakerFullAccess** policy. Then, click on **Next: Review**.

Lastly, give this role a name. Make sure you use a name that you will remember later on, for example `LambdaSageMakerRole`. Then, click on **Create role**.

#### Part B: Create a Lambda function

Now it is time to actually create the Lambda function.

Using the AWS Console, navigate to the AWS Lambda page and click on **Create a function**. When you get to the next page, make sure that **Author from scratch** is selected. Now, name your Lambda function, using a name that you will remember later on, for example `sentiment_analysis_func`. Make sure that the **Python 3.6** runtime is selected and then choose the role that you created in the previous part. Then, click on **Create Function**.

On the next page you will see some information about the Lambda function you've just created. If you scroll down you should see an editor in which you can write the code that will be executed when your Lambda function is triggered. In our example, we will use the code below. 

```python
# We need to use the low-level library to interact with SageMaker since the SageMaker API
# is not available natively through Lambda.
import boto3

def lambda_handler(event, context):

    # The SageMaker runtime is what allows us to invoke the endpoint that we've created.
    runtime = boto3.Session().client('sagemaker-runtime')

    # Now we use the SageMaker runtime to invoke our endpoint, sending the review we were given
    response = runtime.invoke_endpoint(EndpointName = '**ENDPOINT NAME HERE**',    # The name of the endpoint we created
                                       ContentType = 'text/plain',                 # The data format that is expected
                                       Body = event['body'])                       # The actual review

    # The response is an HTTP response whose body contains the result of our inference
    result = response['Body'].read().decode('utf-8')

    return {
        'statusCode' : 200,
        'headers' : { 'Content-Type' : 'text/plain', 'Access-Control-Allow-Origin' : '*' },
        'body' : result
    }
```

Once you have copy and pasted the code above into the Lambda code editor, replace the `**ENDPOINT NAME HERE**` portion with the name of the endpoint that we deployed earlier. You can determine the name of the endpoint using the code cell below.

In [129]:
#predictor
estimator.endpoint

AttributeError: 'PyTorch' object has no attribute 'endpoint'

Once you have added the endpoint name to the Lambda function, click on **Save**. Your Lambda function is now up and running. Next we need to create a way for our web app to execute the Lambda function.

### Setting up API Gateway

Now that our Lambda function is set up, it is time to create a new API using API Gateway that will trigger the Lambda function we have just created.

Using AWS Console, navigate to **Amazon API Gateway** and then click on **Get started**.

On the next page, make sure that **New API** is selected and give the new api a name, for example, `sentiment_analysis_api`. Then, click on **Create API**.

Now we have created an API, however it doesn't currently do anything. What we want it to do is to trigger the Lambda function that we created earlier.

Select the **Actions** dropdown menu and click **Create Method**. A new blank method will be created, select its dropdown menu and select **POST**, then click on the check mark beside it.

For the integration point, make sure that **Lambda Function** is selected and click on the **Use Lambda Proxy integration**. This option makes sure that the data that is sent to the API is then sent directly to the Lambda function with no processing. It also means that the return value must be a proper response object as it will also not be processed by API Gateway.

Type the name of the Lambda function you created earlier into the **Lambda Function** text entry box and then click on **Save**. Click on **OK** in the pop-up box that then appears, giving permission to API Gateway to invoke the Lambda function you created.

The last step in creating the API Gateway is to select the **Actions** dropdown and click on **Deploy API**. You will need to create a new Deployment stage and name it anything you like, for example `prod`.

You have now successfully set up a public API to access your SageMaker model. Make sure to copy or write down the URL provided to invoke your newly created public API as this will be needed in the next step. This URL can be found at the top of the page, highlighted in blue next to the text **Invoke URL**.

## Step 4: Deploying our web app

Now that we have a publicly available API, we can start using it in a web app. For our purposes, we have provided a simple static html file which can make use of the public api you created earlier.

In the `website` folder there should be a file called `index.html`. Download the file to your computer and open that file up in a text editor of your choice. There should be a line which contains **\*\*REPLACE WITH PUBLIC API URL\*\***. Replace this string with the url that you wrote down in the last step and then save the file.

Now, if you open `index.html` on your local computer, your browser will behave as a local web server and you can use the provided site to interact with your SageMaker model.

If you'd like to go further, you can host this html file anywhere you'd like, for example using github or hosting a static site on Amazon's S3. Once you have done this you can share the link with anyone you'd like and have them play with it too!

> **Important Note** In order for the web app to communicate with the SageMaker endpoint, the endpoint has to actually be deployed and running. This means that you are paying for it. Make sure that the endpoint is running when you want to use the web app but that you shut it down when you don't need it, otherwise you will end up with a surprisingly large AWS bill.

**TODO:** Make sure that you include the edited `index.html` file in your project submission.

Now that your web app is working, trying playing around with it and see how well it works.

**Question**: Give an example of a review that you entered into your web app. What was the predicted sentiment of your example review?

**Answer:**

### Delete the endpoint

Remember to always shut down your endpoint if you are no longer using it. You are charged for the length of time that the endpoint is running so if you forget and leave it on you could end up with an unexpectedly large bill.

In [ ]:
predictor.delete_endpoint()